In [3]:
import os
import requests
from dotenv import load_dotenv
import sqlite3
import time

In [4]:
load_dotenv()

API_KEY = os.getenv('UNISWAP_API_KEY') # Fetching the Etherscan API key from environment variables

if not API_KEY: 
    raise ValueError('Please set the UNISWAP_API_KEY environment variable.')

In [ ]:
# Creating a database to store contracts, EOA and tokens

import sqlite3

conn = sqlite3.connect("uniswap.db")
cur = conn.cursor()

cur.execute("""
CREATE TABLE IF NOT EXISTS transactions (
    tx_hash TEXT PRIMARY KEY,
    block_number INTEGER,
    timestamp INTEGER,
    from_address TEXT,
    to_address TEXT,
    token_symbol TEXT,
    value_raw TEXT,        -- raw from Etherscan (wei)
    value_scaled REAL,     -- human-readable ETH/token
    tx_type TEXT,     -- normal, internal, token
    category TEXT,    -- EOA --> Contract, Contract --> Contract, Contract --> EOA
    raw JSON
)
""")
conn.commit()

In [9]:
# EOA → Contract: typical user calling a protocol 
# Contract → Contract: smart contract calling Uniswap V3 Router 

address = "0xE592427A0AEce92De3Edee1F18E0157C05861564" # Uniswap V3 Router contract address

# Helper function to get transactions with pagination
def get_transactions(action="txlist", chainid=1, offset=1000, max_pages=5):
    normal_txs = []
    for page in range(1, max_pages + 1):
        url = (
            f"https://api.etherscan.io/v2/api"
            f"?chainid={chainid}"
            f"&module=account"
            f"&action={action}"
            f"&address={address}"
            f"&startblock=0"
            f"&endblock=latest"
            f"&page={page}"
            f"&offset={offset}"
            f"&sort=desc"
            f"&apikey={API_KEY}"
        )
        response = requests.get(url).json()
        txs = response.get("result", [])
        if not txs:  # Stop if no more results
            break
        normal_txs.extend(txs)
        print(f"Fetched page {page}, got {len(txs)} transactions")

        time.sleep(0.2)  # Helps with API rate limits

    return normal_txs

# Without caching, every time you see an address --> make an API call --> Etherscan tells you if it’s contract or not. Works fine, but very slow
# With caching, first time you see an address --> make API call --> save the result (True = contract, False = EOA).
# Next time you see the same address --> look it up in memory --> instant answer.

contract_cache = {}

def is_contract(address):
    if address in contract_cache:          # Already checked this address
        return contract_cache[address]

    # Otherwise call Etherscan
    url = f"https://api.etherscan.io/api?module=proxy&action=eth_getCode&address={address}&tag=latest&apikey={API_KEY}"
    response = requests.get(url).json()
    result = response["result"] != "0x"  # True if contract, False if EOA

    contract_cache[address] = result       # Save result in cache
    return result

# Differentiate transactions with EOA/Contract labeling
def transactions(txs):
    normal = []
    for tx in txs:
        from_addr = tx["from"]
        to_addr = tx["to"]
        tx["from_type"] = "Contract" if is_contract(from_addr) else "EOA"
        tx["to_type"]   = "Contract" if is_contract(to_addr) else "EOA"
        normal.append(tx)
    return normal

# Fetch up to 5000 normal txs
normal_uniswap_tx = get_transactions("txlist", offset=1000, max_pages=5)
uniswap_n_tx = transactions(normal_uniswap_tx)

for tx in uniswap_n_tx[:10]:  # Show first 10
    print(
        f"TxHash: {tx['hash']} | From: {tx['from']} ({tx['from_type']}) | To: {tx['to']} ({tx['to_type']})"
    )

Fetched page 1, got 1000 transactions
Fetched page 2, got 1000 transactions
Fetched page 3, got 1000 transactions
Fetched page 4, got 1000 transactions
Fetched page 5, got 1000 transactions
TxHash: 0x4df7980aaf09db72a7cd8888667f721cd878465391294f744f8f304a9b907701 | From: 0xf5213a6a2f0890321712520b8048d9886c1a9900 (EOA) | To: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract)
TxHash: 0x9723a14d67bac83ee18a16a982cd124bad74e5241ec00dbbd4bd9064e88cfb7c | From: 0xf5213a6a2f0890321712520b8048d9886c1a9900 (EOA) | To: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract)
TxHash: 0xe0992739311cd8a5fc1ae1acf9f7d12dbd7f45b455af040ba9a6f0542b39b5fe | From: 0xf5213a6a2f0890321712520b8048d9886c1a9900 (EOA) | To: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract)
TxHash: 0xd0580b4ae116b665b29739b593fa22c2fb8ec1c6c78afefc7745fbef0f3b2a12 | From: 0xf5213a6a2f0890321712520b8048d9886c1a9900 (EOA) | To: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract)
TxHash: 0x054af7ca2cf177581f8ebaf502a9d78a

In [10]:
user_to_contract = [tx for tx in uniswap_n_tx if tx["from_type"] == "EOA" and tx["to_type"] == "Contract"]
user_to_contract

[{'blockNumber': '23363538',
  'timeStamp': '1757879639',
  'hash': '0x4df7980aaf09db72a7cd8888667f721cd878465391294f744f8f304a9b907701',
  'nonce': '490160',
  'blockHash': '0x35721f56c7518a9c57fccfbdd2a6453989f1093aa5b264e41dba3d10de0a552b',
  'transactionIndex': '150',
  'from': '0xf5213a6a2f0890321712520b8048d9886c1a9900',
  'to': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'value': '0',
  'gas': '517745',
  'gasPrice': '197893706',
  'isError': '0',
  'txreceipt_status': '1',
  'input': '0x414bf3890000000000000000000000001f9840a85d5af5bf1d1762f925bdaddc4201f984000000000000000000000000c02aaa39b223fe8d0a0e5c4f27ead9083c756cc20000000000000000000000000000000000000000000000000000000000000bb8000000000000000000000000f5213a6a2f0890321712520b8048d9886c1a99000000000000000000000000000000000000000000000000000000000068c71d5c00000000000000000000000000000000000000000000000de54df0804fb300000000000000000000000000000000000000000000000000000740eb74f64db9000000000000000000000000000000000000000000

In [11]:
contract_to_contract = [tx for tx in uniswap_n_tx if tx["from_type"] == "Contract" and tx["to_type"] == "Contract"]
contract_to_contract

[{'blockNumber': '23362892',
  'timeStamp': '1757871851',
  'hash': '0x3295c9b25238b45034411f80abed657139c34533830cad0f8f801cd82f94b2ad',
  'nonce': '90',
  'blockHash': '0x1fb29f9288e33cf5a2bf78c55ff3d71e8dc9b158ea2df31a00a3d7bb8d38b641',
  'transactionIndex': '3',
  'from': '0x67a073a253ad9fd18f726ded8080f3d65c2cf469',
  'to': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'value': '3000000000000000',
  'gas': '557511',
  'gasPrice': '3190876911',
  'isError': '0',
  'txreceipt_status': '1',
  'input': '0x414bf389000000000000000000000000c02aaa39b223fe8d0a0e5c4f27ead9083c756cc2000000000000000000000000163f8c2467924be0ae7b5347228cabf2603187530000000000000000000000000000000000000000000000000000000000000bb800000000000000000000000067a073a253ad9fd18f726ded8080f3d65c2cf4690000000000000000000000000000000000000000000000000000000068c6ff5b000000000000000000000000000000000000000000000000000aa87bee538000000000000000000000000000000000000000000000000000318516ccdcdc0d93000000000000000000000000000000

In [12]:
# An internal transaction isn’t a real transaction broadcast to the chain, It’s a log of value transfers or contract calls that happen inside the execution of a top-level transaction.
# Example: Alice (EOA) calls Uniswap Router --> The Router calls a Pool contract --> The Pool sends ETH back to Alice.
# Contract --> EOA: That happens when a contract sends ETH or tokens back to a wallet inside the execution.

address = "0xE592427A0AEce92De3Edee1F18E0157C05861564"  # Uniswap V3 Router

def get_transactions(action="txlistinternal", chainid=1, offset=1000, max_pages=5):
    internal_tx = []
    for page in range(1, max_pages + 1):
        url = (
            f"https://api.etherscan.io/v2/api"
            f"?chainid={chainid}"
            f"&module=account"
            f"&action={action}"
            f"&address={address}"
            f"&startblock=0"
            f"&endblock=latest"
            f"&page={page}"
            f"&offset={offset}"
            f"&sort=desc"
            f"&apikey={API_KEY}"
        )
        response = requests.get(url).json()
        txs_internal = response.get("result", [])
        if not txs_internal:  # Stop if no more results
            break
        internal_tx.extend(txs_internal)
        print(f"Fetched page {page}, got {len(txs_internal)} transactions")

        time.sleep(0.2)  # Helps with API rate limits

    return internal_tx

contract_cache = {}

def is_contract(address):
    if address in contract_cache:          # Already checked this address
        return contract_cache[address]

    # Otherwise call Etherscan
    url = f"https://api.etherscan.io/api?module=proxy&action=eth_getCode&address={address}&tag=latest&apikey={API_KEY}"
    response = requests.get(url).json()
    result = response["result"] != "0x"  # True if contract, False if EOA

    contract_cache[address] = result       # Save result in cache
    return result

# Enrichment
def internal_transactions(txs):
    internal = []
    for tx in txs:
        from_addr = tx.get("from")
        to_addr   = tx.get("to")
        tx["from_type"] = "Contract" if is_contract(from_addr) else "EOA"
        tx["to_type"]   = "Contract" if to_addr and is_contract(to_addr) else "EOA"
        internal.append(tx)
    return internal

# Fetch up to 5000 normal txs
internal_uniswap_tx = get_transactions("txlistinternal", offset=1000, max_pages=5)
uniswap_internal = internal_transactions(internal_uniswap_tx)

for tx in uniswap_internal[:10]:  # Show first 10
    print(
        f"TxHash: {tx['hash']} | From: {tx['from']} | {tx['from_type']} | To: {tx['to']} | {tx['to_type']}"
    )


Fetched page 1, got 1000 transactions
Fetched page 2, got 1000 transactions
Fetched page 3, got 1000 transactions
Fetched page 4, got 1000 transactions
Fetched page 5, got 1000 transactions
TxHash: 0xf05c4956cf82e8a01ad26c2dcdbf572ccba2aee21134d452fe10a502e5d346c4 | From: 0xe592427a0aece92de3edee1f18e0157c05861564 | Contract | To: 0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2 | Contract
TxHash: 0xf05c4956cf82e8a01ad26c2dcdbf572ccba2aee21134d452fe10a502e5d346c4 | From: 0x6aa981bff95edfea36bdae98c26b274ffcafe8d3 | Contract | To: 0xe592427a0aece92de3edee1f18e0157c05861564 | Contract
TxHash: 0x2a7550329e27b428b03a876bb58953aa4aaaf5db2655d2ef3cfd32fa25cc8ffb | From: 0xe592427a0aece92de3edee1f18e0157c05861564 | Contract | To: 0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2 | Contract
TxHash: 0x2a7550329e27b428b03a876bb58953aa4aaaf5db2655d2ef3cfd32fa25cc8ffb | From: 0xaa390a37006e22b5775a34f2147f81ebd6a63641 | Contract | To: 0xe592427a0aece92de3edee1f18e0157c05861564 | Contract
TxHash: 0xc1f9d797658a

In [10]:
internal_contract_to_contract = [tx for tx in uniswap_internal if tx["from_type"] == "Contract" and tx["to_type"] == "Contract"]
internal_contract_to_contract

[{'blockNumber': '23363205',
  'timeStamp': '1757875619',
  'hash': '0x4e2e4df82aa8df355e48b18f22550a7803e5b364dc37f0a53ec262815ba5f324',
  'from': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'to': '0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2',
  'value': '20762400000000000',
  'contractAddress': '',
  'input': '',
  'type': 'call',
  'gas': '205329',
  'gasUsed': '23974',
  'traceId': '0_1_1_1_1_1_1',
  'isError': '0',
  'errCode': '',
  'from_type': 'Contract',
  'to_type': 'Contract'},
 {'blockNumber': '23363205',
  'timeStamp': '1757875619',
  'hash': '0x4e2e4df82aa8df355e48b18f22550a7803e5b364dc37f0a53ec262815ba5f324',
  'from': '0x6aa981bff95edfea36bdae98c26b274ffcafe8d3',
  'to': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'value': '20762400000000000',
  'contractAddress': '',
  'input': '',
  'type': 'call',
  'gas': '301762',
  'gasUsed': '120986',
  'traceId': '0_1_1_1',
  'isError': '0',
  'errCode': '',
  'from_type': 'Contract',
  'to_type': 'Contract'},
 {'blockNum

In [14]:
contract_to_user = [tx for tx in uniswap_internal if tx["from_type"] == "Contract" and tx["to_type"] == "EOA"]
contract_to_user

[{'blockNumber': '23363595',
  'timeStamp': '1757880335',
  'hash': '0xc1f9d797658a01917829f2c07d98e16abf8e8c684762c3bf168b782e7fe68d13',
  'from': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'to': '0x3515caf8e774bbfccf65f19af812e5b7c51e3387',
  'value': '128694499670305382',
  'contractAddress': '',
  'input': '',
  'type': 'call',
  'gas': '146784',
  'gasUsed': '0',
  'traceId': '0_1_1',
  'isError': '0',
  'errCode': '',
  'from_type': 'Contract',
  'to_type': 'EOA'},
 {'blockNumber': '23363594',
  'timeStamp': '1757880323',
  'hash': '0xb744002d43be6454c00f8e39eb898f687826659c35ac57a49031c0f4539e9569',
  'from': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'to': '0x972a886bf1e81637671f89d4a5fd1a7c38f89495',
  'value': '171157455557427604',
  'contractAddress': '',
  'input': '',
  'type': 'call',
  'gas': '146809',
  'gasUsed': '0',
  'traceId': '0_1_1',
  'isError': '0',
  'errCode': '',
  'from_type': 'Contract',
  'to_type': 'EOA'},
 {'blockNumber': '23363578',
  'timeSt

In [19]:
address = "0xE592427A0AEce92De3Edee1F18E0157C05861564"  # Uniswap V3 Router
contract_cache = {}

def get_token_transactions(action="tokentx", chainid=1, offset=1000, max_pages=5):
    tx_token = []
    for page in range(1, max_pages + 1):
        url = (
            f"https://api.etherscan.io/v2/api"
            f"?chainid={chainid}"
            f"&module=account"
            f"&action={action}"
            f"&address={address}"
            f"&startblock=0"
            f"&endblock=latest"
            f"&page={page}"
            f"&offset={offset}"
            f"&sort=desc"
            f"&apikey={API_KEY}"
        )
        
        response = requests.get(url).json()
        tokentxs = response.get("result", [])
        if not tokentxs:  # Stop if no more results
            break
        tx_token.extend(tokentxs)
        print(f"Fetched page {page}, got {len(tokentxs)} transactions")

        time.sleep(0.2)  # Helps with API rate limits

    return tx_token


def is_contract(address):
    if address in contract_cache:  # Already checked
        return contract_cache[address]

    url = f"https://api.etherscan.io/api?module=proxy&action=eth_getCode&address={address}&tag=latest&apikey={API_KEY}"
    response = requests.get(url).json()
    result = response["result"] != "0x"  # True if contract, False if EOA

    contract_cache[address] = result
    return result


def classify_addresses(txs):
    """Remove duplicate and classify all unique addresses"""
    unique_addresses = set()
    for tx in txs:
        unique_addresses.add(tx["from"])
        unique_addresses.add(tx["to"])

    labels = {}
    for addr in unique_addresses:
        labels[addr] = "Contract" if is_contract(addr) else "EOA"
        time.sleep(0.1)  # avoid hitting rate limit
    return labels


def token_txs(txs, labels):
    token = []
    for tx in txs:
        tx["from_type"] = labels.get(tx["from"], "Unknown")
        tx["to_type"]   = labels.get(tx["to"], "Unknown")

        decimals = int(tx.get("tokenDecimal", 0))
        tx["value_scaled"] = int(tx["value"]) / (10 ** decimals) if decimals else int(tx["value"])

        token.append(tx)
    return token


# Fetch up to 5000 token txs
uniswap_token_tx = get_token_transactions("tokentx", offset=1000, max_pages=5)

# Classify unique addresses once
labels = classify_addresses(uniswap_token_tx)

# With scaled values + EOA/Contract types
uniswap_tokens = token_txs(uniswap_token_tx, labels)

# Show first 10
for tx in uniswap_tokens[:10]:
    print(
        f"TxHash: {tx['hash']} | Token: {tx['tokenSymbol']} | "
        f"From: {tx['from']} ({tx['from_type']}) | "
        f"To: {tx['to']} ({tx['to_type']}) | "
        f"Value: {tx['value_scaled']}"
    )


Fetched page 1, got 1000 transactions
Fetched page 2, got 1000 transactions
Fetched page 3, got 1000 transactions
Fetched page 4, got 1000 transactions
Fetched page 5, got 1000 transactions
TxHash: 0x48d6ef6ba50ea5c3351c51f04c9f3a0f8154c36e27aec85f5bf0bf9b1e8a36ae | Token: WETH | From: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract) | To: 0x826b34e62320108a9fa38a080360d693a8a73111 (Contract) | Value: 0.10593694928050378
TxHash: 0x48d6ef6ba50ea5c3351c51f04c9f3a0f8154c36e27aec85f5bf0bf9b1e8a36ae | Token: WETH | From: 0xc7bbec68d12a0d1830360f8ec58fa599ba1b0e9b (Contract) | To: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract) | Value: 0.10593694928050378
TxHash: 0x3c57bbd9aaf424092122814ab32f39a47b068ae213687c968ad2d6534579ba64 | Token: WETH | From: 0xe592427a0aece92de3edee1f18e0157c05861564 (Contract) | To: 0xc45a81bc23a64ea556ab4cdf08a86b61cdceea8b (Contract) | Value: 0.004242094569403703
TxHash: 0x839950a50bac59dbb9ee89f9377e4a6b5b87022a03dd605fe9c55304f61ad213 | Token: WETH 

In [28]:
def transaction_type(tx, tx_type):
    tx["tx_type"] = tx_type

    # Token-specific scaling
    if tx_type == "erc20":
        decimals = int(tx.get("tokenDecimal", 0))
        tx["value_scaled"] = int(tx["value"]) / (10 ** decimals) if decimals else int(tx["value"])
    else:
        tx["value_scaled"] = int(tx.get("value", 0))

    # Placeholder logic for EOA/Contract labeling
    # If you don’t want to call Etherscan for is_contract(),
    # you could just leave this as "Unknown"
    tx["from_type"] = tx.get("from_type", "Unknown")
    tx["to_type"]   = tx.get("to_type", "Unknown")

    # Category now depends on both tx_type and address types
    tx["category"] = categorize(tx_type, tx["from_type"], tx["to_type"])

    return tx

def categorize(tx_type, from_type, to_type):
    if tx_type == "normal":
        if from_type == "EOA" and to_type == "Contract":
            return "EOA-Contract"
        elif from_type == "Contract" and to_type == "Contract":
            return "Contract-Contract"
        else:
            return "Other"

    elif tx_type == "internal":
        if from_type == "Contract" and to_type == "Contract":
            return "Contract-Contract"
        elif from_type == "Contract" and to_type == "EOA":
            return "Contract-EOA"
        else:
            return "Other"

    elif tx_type == "erc20":
        if from_type == "Contract" and to_type == "Contract":
            return "Contract-Contract Token Transfer"
        elif from_type == "EOA" and to_type == "Contract":
            return "EOA-Contract Token Transfer"
        else:
            return "Other Token Transfer"

    return "Unknown"


In [32]:
normal_transactions   = [transaction_type(tx, "normal") for tx in normal_uniswap_tx]
internal_transactions = [transaction_type(tx, "internal") for tx in internal_uniswap_tx]
token_transactions    = [transaction_type(tx, "erc20") for tx in uniswap_token_tx]

token_transactions

[{'blockNumber': '23363972',
  'timeStamp': '1757884871',
  'hash': '0x48d6ef6ba50ea5c3351c51f04c9f3a0f8154c36e27aec85f5bf0bf9b1e8a36ae',
  'nonce': '47061',
  'blockHash': '0x390ab822b08f9205d6c6667a87b4c4638dec70a691fec0f88836f1f49e182417',
  'from': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'contractAddress': '0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2',
  'to': '0x826b34e62320108a9fa38a080360d693a8a73111',
  'value': '105936949280503780',
  'tokenName': 'Wrapped Ether',
  'tokenSymbol': 'WETH',
  'tokenDecimal': '18',
  'transactionIndex': '8',
  'gas': '767414',
  'gasPrice': '2129002139',
  'gasUsed': '260992',
  'cumulativeGasUsed': '2698404',
  'input': 'deprecated',
  'methodId': '0x0b894c86',
  'functionName': '',
  'confirmations': '8',
  'from_type': 'Contract',
  'to_type': 'Contract',
  'value_scaled': 0.10593694928050378,
  'tx_type': 'erc20',
  'category': 'Contract-Contract Token Transfer'},
 {'blockNumber': '23363972',
  'timeStamp': '1757884871',
  'hash': '0x4

In [33]:
internal_transactions

[{'blockNumber': '23363623',
  'timeStamp': '1757880671',
  'hash': '0xf05c4956cf82e8a01ad26c2dcdbf572ccba2aee21134d452fe10a502e5d346c4',
  'from': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'to': '0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2',
  'value': '3936000000000000',
  'contractAddress': '',
  'input': '',
  'type': 'call',
  'gas': '230963',
  'gasUsed': '23974',
  'traceId': '0_1_1_1_1_1_1',
  'isError': '0',
  'errCode': '',
  'from_type': 'Contract',
  'to_type': 'Contract',
  'tx_type': 'internal',
  'value_scaled': 3936000000000000,
  'category': 'Contract-Contract'},
 {'blockNumber': '23363623',
  'timeStamp': '1757880671',
  'hash': '0xf05c4956cf82e8a01ad26c2dcdbf572ccba2aee21134d452fe10a502e5d346c4',
  'from': '0x6aa981bff95edfea36bdae98c26b274ffcafe8d3',
  'to': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'value': '3936000000000000',
  'contractAddress': '',
  'input': '',
  'type': 'call',
  'gas': '328588',
  'gasUsed': '120938',
  'traceId': '0_1_1_1',
  'is

In [34]:
normal_transactions

[{'blockNumber': '23363538',
  'timeStamp': '1757879639',
  'hash': '0x4df7980aaf09db72a7cd8888667f721cd878465391294f744f8f304a9b907701',
  'nonce': '490160',
  'blockHash': '0x35721f56c7518a9c57fccfbdd2a6453989f1093aa5b264e41dba3d10de0a552b',
  'transactionIndex': '150',
  'from': '0xf5213a6a2f0890321712520b8048d9886c1a9900',
  'to': '0xe592427a0aece92de3edee1f18e0157c05861564',
  'value': '0',
  'gas': '517745',
  'gasPrice': '197893706',
  'isError': '0',
  'txreceipt_status': '1',
  'input': '0x414bf3890000000000000000000000001f9840a85d5af5bf1d1762f925bdaddc4201f984000000000000000000000000c02aaa39b223fe8d0a0e5c4f27ead9083c756cc20000000000000000000000000000000000000000000000000000000000000bb8000000000000000000000000f5213a6a2f0890321712520b8048d9886c1a99000000000000000000000000000000000000000000000000000000000068c71d5c00000000000000000000000000000000000000000000000de54df0804fb300000000000000000000000000000000000000000000000000000740eb74f64db9000000000000000000000000000000000000000000

In [ ]:
# Fetch data
normal_uniswap_tx = get_transactions("txlist")
internal_uniswap_tx = get_transactions("txlistinternal")
uniswap_token_tx = get_transactions("tokentx")

# Combine and classify
combined = []

for tx in normal_tx:
    combined.append({
        "txHash": tx['hash'],
        "from": tx['from'],
        "to": tx['to'],
        "value": tx['value'],
        "type_from": "Contract" if is_contract(tx['from']) else "EOA",
        "type_to": "Contract" if is_contract(tx['to']) else "EOA",
        "internal": False,
        "tokenTransfer": False,
        "blockNumber": tx['blockNumber']
    })

for tx in internal_tx:
    combined.append({
        "txHash": tx['hash'],
        "from": tx['from'],
        "to": tx['to'],
        "value": tx['value'],
        "type_from": "Contract" if is_contract(tx['from']) else "EOA",
        "type_to": "Contract" if is_contract(tx['to']) else "EOA",
        "internal": True,
        "tokenTransfer": False,
        "blockNumber": tx['blockNumber']
    })

for tx in token_tx:
    combined.append({
        "txHash": tx['hash'],
        "from": tx['from'],
        "to": tx['to'],
        "value": tx['value'],
        "type_from": "Contract" if is_contract(tx['from']) else "EOA",
        "type_to": "Contract" if is_contract(tx['to']) else "EOA",
        "internal": False,
        "tokenTransfer": True,
        "blockNumber": tx['blockNumber']
    })

print(f"Total combined transactions: {len(combined)}")
